# Connect and fetch data from Neo4j DB

In [1]:
!pip install neo4j

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 296.6/296.6 kB 4.3 MB/s eta 0:00:00


In [17]:
from neo4j import GraphDatabase
from collections import defaultdict

In [14]:
# Import necessary libraries
import pandas as pd

# Load the CSV file from Google Drive (adjust the path to match your file location)
pd_data = pd.read_csv("https://raw.githubusercontent.com/Addika1630/RAG_Medical_System/refs/heads/main/drugs-indication.csv")

# Display the first few rows of the dataset to understand the structure
print(pd_data.head())

# Filter the relevant columns: 'name', 'primarySubstabce', 'doseAmount', 'doseUnit', 'indication'
# These columns are relevant for drug-disease prediction
drug_data = pd_data[['name', 'indication', 'doseAmount']]

# Display the filtered data
print("\nFiltered Data for Drug, Dose, and Disease Prediction:")
print(drug_data.head())

# RAG Analysis (Retrieve, Augment, Generate):
# Group the drugs by their indications to understand the drug-disease relationships

# Using .iterrows() to iterate over DataFrame rows
data = [(row["name"], row["indication"],  row["doseAmount"])
                           for _, row in drug_data.iterrows()]

# Display the grouped data
print("\nDrug Indication Grouped Data:")
print(data)


   primaryid  drugSequence               role           name primarySubstabce  \
0  100654764             1    Primary Suspect       AFINITOR       EVEROLIMUS   
1  100654764             2  Secondary Suspect      SORAFENIB        SORAFENIB   
2  100654764             3        Concomitant     CLONAZEPAM       CLONAZEPAM   
3  100654764             4        Concomitant  DEXAMETHASONE    DEXAMETHASONE   
4  100654764             5        Concomitant         KEPPRA    LEVETIRACETAM   

  route doseAmount doseUnit    indication  
0  Oral          5       MG  Glioblastoma  
1  Oral        400       MG  Glioblastoma  
2  Oral        0.5       MG       Seizure  
3  Oral          4       MG       Unknown  
4  Oral        100       MG       Unknown  

Filtered Data for Drug, Dose, and Disease Prediction:
            name    indication doseAmount
0       AFINITOR  Glioblastoma          5
1      SORAFENIB  Glioblastoma        400
2     CLONAZEPAM       Seizure        0.5
3  DEXAMETHASONE       Unk

In [15]:
data

[('AFINITOR', 'Glioblastoma', '5'),
 ('SORAFENIB', 'Glioblastoma', '400'),
 ('CLONAZEPAM', 'Seizure', '0.5'),
 ('DEXAMETHASONE', 'Unknown', '4'),
 ('KEPPRA', 'Unknown', '100'),
 ('LISINOPRIL', 'Unknown', '20'),
 ('METOPROLOL SUCCINATE', 'Unknown', '25'),
 ('ONDANSETRON', 'Unknown', '8'),
 ('VIMPAT', 'Seizure', '200'),
 ('SENOKOT', 'Unknown', '1'),
 ('Belimumab', 'Systemic lupus erythematosus', '10'),
 ('PREDNISONE', 'Systemic lupus erythematosus', '5'),
 ('NEUPOGEN', 'Autoimmune neutropenia', '300'),
 ('VANCOMYCIN', 'Infection', '1'),
 ('FLAGYL', 'Infection', '500'),
 ('VORICONAZOLE', 'Infection', '250'),
 ('REVLIMID', 'Plasma cell myeloma', '15'),
 ('DECADRON', 'Plasma cell myeloma', '20'),
 ('LYRICA', 'Neuralgia', '200'),
 ('FABRAZYME', "Fabry's disease", '70'),
 ('PREDNISONE', 'Premedication', '30'),
 ('HYDROXYZINE', 'Premedication', '50'),
 ('LYRICA', 'Diabetic neuropathy', '50'),
 ('LYRICA', 'Pain in extremity', '75'),
 ('METOPROLOL', 'Unknown', '100'),
 ('RANITIDINE', 'Dyspepsia'

# Transform and Group

In [18]:
context_data = defaultdict(list)
for name, indication, doseAmount in data:
    try:
        # Attempt to convert doseAmount to float
        context_data[name].append((indication, float(doseAmount)))
    except ValueError:
        # Handle the error (skip or log, depending on requirements)
        pass


grouped_data = {}
for name, details in context_data.items():
    total_doseAmount = sum(doseAmount for _, doseAmount in details)
    indications = [indication for indication, _ in details]
    grouped_data[name] = {"total_doseAmount": total_doseAmount, "indications": indications}

print(grouped_data)



{'AFINITOR': {'total_doseAmount': 48.5, 'indications': ['Glioblastoma', 'Astrocytoma, low grade', 'Seizure', 'Unknown', 'Unknown', 'Astrocytoma, low grade', 'Unknown']}, 'SORAFENIB': {'total_doseAmount': 400.0, 'indications': ['Glioblastoma']}, 'CLONAZEPAM': {'total_doseAmount': 34.125, 'indications': ['Seizure', 'Anxiety', 'Unknown', 'Unknown', 'Anxiety', 'Unknown', 'Schizoaffective disorder', 'Insomnia', 'Generalised anxiety disorder', 'Depression', 'Unknown', 'Unknown', 'Unknown', 'Unknown', 'Muscle spasticity', 'Unknown', 'Unknown', 'Anxiety', 'Unknown', 'Unknown', 'Unknown', 'Unknown', 'Unknown', 'Unknown', 'Anxiety', 'Unknown', 'Drug withdrawal syndrome', 'Unknown', 'Unknown', 'Unknown', 'Unknown', 'Unknown']}, 'DEXAMETHASONE': {'total_doseAmount': 2587.25, 'indications': ['Unknown', 'Plasma cell myeloma', 'Plasma cell myeloma', 'Plasma cell myeloma', 'Plasma cell myeloma', 'Plasma cell myeloma', 'Plasma cell myeloma', 'Plasma cell myeloma', 'Unknown', 'Plasma cell myeloma', 'Unk

In [19]:
# Changing the dict data into Graph like representation
!pip install networkx


In [ ]:
import networkx as nx
G = nx.Graph()

# Add nodes and edges from the dictionary
for name, details in grouped_data.items():
    G.add_node(name, total_=details["total_doseAmount"])
    for indication in details["indications"]:
        G.add_edge(name, indication)

# Check the created graph
print("Nodes of graph:", G.nodes(data=True))
print("Edges of graph:", G.edges())

Nodes of graph: [('AFINITOR', {'total_': 48.5}), ('Glioblastoma', {}), ('Astrocytoma, low grade', {}), ('Seizure', {}), ('Unknown', {}), ('SORAFENIB', {'total_': 400.0}), ('CLONAZEPAM', {'total_': 34.125}), ('Anxiety', {}), ('Schizoaffective disorder', {}), ('Insomnia', {}), ('Generalised anxiety disorder', {}), ('Depression', {}), ('Muscle spasticity', {}), ('Drug withdrawal syndrome', {}), ('DEXAMETHASONE', {'total_': 2587.25}), ('Plasma cell myeloma', {}), ('Nausea', {}), ('Premedication', {}), ('Plasma cell myeloma refractory', {}), ('Spinal cord oedema', {}), ('Acute lymphocytic leukaemia', {}), ('B precursor type acute leukaemia', {}), ('Prophylaxis', {}), ('Pancytopenia', {}), ('Oral candidiasis', {}), ('T-cell type acute leukaemia', {}), ('Chemotherapy side effect prophylaxis', {}), ('Oedema', {}), ('Prophylaxis of nausea and vomiting', {}), ('Diffuse large B-cell lymphoma', {}), ('Cytokine release syndrome', {}), ('Swelling', {}), ('Encephalopathy', {}), ('Stomatitis', {}), ('

# Embeddings

In [20]:
!pip install node2vec
!pip install langchain-community
!pip install llama-index
!pip install sentence-transformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 50.6/50.6 kB 3.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.4/2.4 MB 28.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 40.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 407.7/407.7 kB 23.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 296.7/296.7 kB 17.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.4/76.4 kB 5.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.0/78.0 kB 5.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.5/49.5 kB 3.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 144.5/144.5 kB 9.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.5/54.5 kB 3.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 4.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 17.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 39

In [21]:
# alternative embedding
from langchain.embeddings import HuggingFaceEmbeddings, SentenceTransformerEmbeddings
from llama_index.legacy.embeddings.langchain import LangchainEmbedding

embed_model = LangchainEmbedding(
  HuggingFaceEmbeddings(model_name="sentence-transformers/all-mpnet-base-v2")
)

[nltk_data] Downloading package stopwords to
[nltk_data]     /usr/local/lib/python3.10/dist-
[nltk_data]     packages/llama_index/legacy/_static/nltk_cache...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to
[nltk_data]     /usr/local/lib/python3.10/dist-
[nltk_data]     packages/llama_index/legacy/_static/nltk_cache...
[nltk_data]   Unzipping tokenizers/punkt.zip.
<ipython-input-21-8f50356297b5>:6: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-huggingface package and should be used instead. To use it run `pip install -U :class:`~langchain-huggingface` and import as `from :class:`~langchain_huggingface import HuggingFaceEmbeddings``.
  HuggingFaceEmbeddings(model_name="sentence-transformers/all-mpnet-base-v2")
/usr/local/lib/python3.10/dist-packages/sentence_transformers/cross_encoder/CrossEncoder.py:13: T

modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.6k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

...

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/239 [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [25]:
# grouped_data

# Embed player names with additional context
embeddings = {}
for name, details in grouped_data.items():
    context = f"{name} drug taken a total of {details['total_doseAmount']} MG for the disease: {', '.join(details['indications'])}"
    embeddings[name] = embed_model.get_text_embedding(context)

# Connect to pinecone

In [22]:
!pip install pinecone-client

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 244.8/244.8 kB 5.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 85.4/85.4 kB 6.0 MB/s eta 0:00:00


In [ ]:
# Initialize Pinecone
import pinecone
import numpy as np
from pinecone import ServerlessSpec # Import ServerlessSpec


pine_api = "a4228145-908e-43ee-b253-d2f5aac490c3"

pinecone_client = pinecone.Pinecone(api_key=pine_api)

index_name = "nba-players-index"

# Use the Pinecone instance to create the index:
if index_name not in pinecone_client.list_indexes().names():
    pinecone_client.create_index(index_name, dimension=5000, spec=ServerlessSpec(
                cloud='aws',
                region='us-east-1'
            ))

# Use the Pinecone instance to get the index:
index = pinecone_client.Index(index_name)

# Upsert embeddings to Pinecone
for name, vector in embeddings.items():
    # Check if vector is a NumPy array before calling tolist()
    # If it's not a NumPy array and it's not already a list, convert it to a list
    if not isinstance(vector, (np.ndarray, list)):
        vector = [vector] # Convert to a list if it's a single element
    elif isinstance(vector, np.ndarray):
        vector = vector.tolist() # Convert numpy array to list

    index.upsert([(name, vector)])  # Upsert with the correctly formatted vector

# Check the generated embeddings
for name, vector in embeddings.items():
    print(f"Drug: {name}, Embedding: {vector}")

Drug: AFINITOR, Embedding: [0.024311762303113937, -0.06367511302232742, -0.0010476558236405253, 0.025406965985894203, -0.02088025026023388, 0.02430085651576519, -0.009035693481564522, 0.05276792496442795, -0.03232476860284805, -0.006731313653290272, -0.009265695698559284, -0.05646095424890518, -0.016049664467573166, 0.039822109043598175, 0.03137044236063957, -0.008909833617508411, -0.015653938055038452, 0.011411038227379322, -0.008204864338040352, -0.05569601431488991, -0.0039023892022669315, 0.0122147835791111, -0.06100861728191376, 0.04327470064163208, -0.00904870219528675, 0.00697094202041626, 0.061469629406929016, -0.05847135931253433, 0.009658711962401867, -0.01001179963350296, 0.01789437048137188, -0.04600659757852554, -0.0235008392482996, 0.025965893641114235, 1.3864872698832187e-06, -0.015791431069374084, 0.024742865934967995, 0.03134501725435257, 0.046973925083875656, -0.059578798711299896, 0.003597918199375272, 0.0019974657334387302, -0.011400604620575905, -0.0050796098075807

In [27]:
# using the same function as in the demo
def get_data_from_db(query):
    # embed query
    xq = embed_model.get_text_embedding(query)
    # query database
    result = index.query(vector=xq, top_k=3, includeMetadata=True)
    matches = []
    for i in result['matches']:
      # filter by score
      if (i['score'] > 0.6):
        # print(i['id'])
        # append best results
        matches.append(i['id'])
    return str(matches)

In [ ]:
mat = index.query(vector=embed_model.get_text_embedding("What are the teams Lebron James played against?"), top_k=3, includeMetadata=True)

In [ ]:
mat['matches'][0]['id']

'LeBron James'

# LLM using together AI

In [28]:

B_INST, E_INST = "[INST]", "[/INST]"
B_SYS, E_SYS = "<<SYS>>\n", "\n<</SYS>>\n\n"
DEFAULT_SYSTEM_PROMPT = """\
You are an AI model tasked with querying a graph database stored in Pinecone. Use the context from the natural languge prompt to query the database and generate the results.
Note: Do not include any explanations or apologies in your responses.
Do not respond to any questions that might ask anything else than for you to construct a retrieve information related to the context.
Do not include any text except the generated output statement.
"""
# DEFAULT_SYSTEM_PROMPT = """Task: Answer querying questions based on the context provided.
# Instructions:
# Use only the provided relationship types and properties in the context.
# Do not use any other relationship types or properties that are not provided. Follow the semantics used in the context.

# Note: Do not include any explanations or apologies in your responses.
# Do not respond to any questions that might ask anything else than for you to construct a Cypher statement.
# Do not include any text except the generated output statement.

# Important: In the generated output, you must explicitly include the property values used in the query's filtering condition, alongside the main information requested from the original question.

# """

SYSTEM_PROMPT = B_SYS + DEFAULT_SYSTEM_PROMPT + E_SYS

def get_prompt(instruction):
    prompt_template =  B_INST + SYSTEM_PROMPT + instruction + E_INST
    return prompt_template

In [32]:
def format_prompt(query, context):
    return '''
    ### Texts:
    {context}

    ### Question:
    {query}
    '''.format(context=context, query=query)

In [29]:
!pip install together

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 68.1/68.1 kB 1.9 MB/s eta 0:00:00


In [30]:
from together import Together
together_api = "0e34e3e9f142636b1161180f3f79fdcb4a0aaeeb31efb34e5e1b821be772fe27"


client = Together(api_key=together_api)

# Define a function that runs the model
def answer(query):
    context = get_data_from_db(query)

    prompt = format_prompt(query, context)
    prompt_template = get_prompt(prompt)

    stream = client.chat.completions.create(
    model="mistralai/Mixtral-8x7B-Instruct-v0.1",
    messages=[{"role": "user", "content": prompt_template}],
    )

    print(stream.choices[0].message.content.replace('```', '').strip())

# stream=True,
    # for chunk in stream:
    #     print(chunk.choices[0].delta.content or "", end="", flush=True)
    # return generate(prompt_template)

In [33]:
answer('How much MG instructions did EVEROLIMUS treat against the Glioblastoma ?')

The total prescribed dosage of Everolimus for treating Glioblastoma is 10 mg per day.


In [34]:
answer('What are the instruction for the Seizure that Concomitant treated?')

The instructions for the seizure concomitant treatment are:

- Brivaracetam: Specific dosage adjustments for seizure concomitant treatment are not mentioned in the database.
- Lacosamide: Specific dosage adjustments for seizure concomitant treatment are not mentioned in the database.
- Vimtec (another name for Vintedge in some regions): Specific dosage adjustments for seizure concomitant treatment are not mentioned in the database.

Please consult a healthcare professional for more detailed information.


# Possible queries